In [ ]:
# import requests
# import pandas as pd
# from bs4 import BeautifulSoup as bs
# import datetime
# import time

# class MetroTVNewsScraper:

#     def __init__(self):
#         """Search URL"""
#         self.search_url = 'https://www.metrotvnews.com'
#         self.headers = {
#             'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36'
#         }

#         # Map Indonesian months to English for parsing
#         self.bulan_map = {
#             'Januari': 'January', 'Februari': 'February', 'Maret': 'March',
#             'April': 'April', 'Mei': 'May', 'Juni': 'June',
#             'Juli': 'July', 'Agustus': 'August', 'September': 'September',
#             'Oktober': 'October', 'November': 'November', 'Desember': 'December'
#         }

#     def parse_indonesian_date(self, date_string: str):
#         """Convert Indonesian date string to date object"""
#         for indo, eng in self.bulan_map.items():
#             date_string = date_string.replace(indo, eng)
#         try:
#             return datetime.datetime.strptime(date_string, '%d %B %Y').date()
#         except ValueError:
#             return None

#     def scrape_latest_articles(self, max_pages: int):
#         """Scrapes the latest articles from Metro TV News"""
#         data = []
        
#         for page_num in range(1, max_pages + 1):
#             if page_num == 1:
#                 url = self.search_url
#             else:
#                 url = f'{self.search_url}/index/{page_num}'
            
#             print(f"Scraping page {page_num}: {url}")

#             try:
#                 response = requests.get(url, headers=self.headers, timeout=10)
#                 response.raise_for_status()
#             except requests.RequestException as e:
#                 print(f"Could not fetch page {page_num}: {e}")
#                 continue

#             time.sleep(2)  # Be polite with delays

#             soup = bs(response.text, "html.parser")
            
#             # Try different selectors for articles
#             articles = soup.find_all("div", class_="most__item") or \
#                        soup.find_all("div", class_="news__item") or \
#                        soup.find_all("article")
            
#             if not articles:
#                 print(f"No articles found on page {page_num} with current selectors.")
#                 break

#             for article in articles:
#                 try:
#                     # Try different selectors for title and link
#                     title_tag = article.find("h3") or article.find("h2") or article.find("h4")
#                     if not title_tag or not title_tag.a:
#                         continue
                    
#                     title = title_tag.a.text.strip()
#                     link = title_tag.a["href"]
                    
#                     # Try to get image
#                     image_tag = article.find("img")
#                     image_url = image_tag["src"] if image_tag and "src" in image_tag.attrs else "No Image"
                    
#                     # Try to get date - Metro TV often puts date in a span with class 'date'
#                     date_tag = article.find("span", class_="date")
#                     post_date = self.parse_indonesian_date(date_tag.text.strip()) if date_tag else None
                    
#                     waktu_scraping = datetime.date.today().strftime("%Y-%m-%d")
                    
#                     data.append([title, link, image_url, post_date, waktu_scraping, False])
                
#                 except Exception as e:
#                     print(f"Error processing an article: {e}")
#                     continue

#         df = pd.DataFrame(data, columns=["Title", "Link", "Image", "Post_Date", "Waktu_Scraping", "Berita Hoax"])
#         return df

# # Usage example:
# scraper = MetroTVNewsScraper()
# news_data = scraper.scrape_latest_articles(max_pages=2)
# print(news_data)

Scraping page 1: https://www.metrotvnews.com
No articles found on page 1 with current selectors.
Empty DataFrame
Columns: [Title, Link, Image, Post_Date, Waktu_Scraping, Berita Hoax]
Index: []


In [25]:
import os
import csv
import time
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin

def scrape_turnbackhoax():
    """
    Scrapes articles and images from multiple pages of turnbackhoax.id 
    and saves the data to a CSV file.
    """
    base_url = "https://turnbackhoax.id/"
    # Set a user-agent header to mimic a web browser
    headers = {
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36"
    }

    # --- SET HOW MANY PAGES TO SCRAPE ---
    num_pages_to_scrape = 500 

    # Create a directory to store images if it doesn't exist
    if not os.path.exists("scraped_images"):
        os.makedirs("scraped_images")

    try:
        # Open a CSV file to write the scraped data
        with open('turnbackhoax_data.csv', 'w', newline='', encoding='utf-8') as csvfile:
            csv_writer = csv.writer(csvfile)
            # Write the header row
            csv_writer.writerow(['Title', 'Content', 'Image Filename'])

            # Loop through the desired number of pages
            for page_num in range(1, num_pages_to_scrape + 1):
                if page_num == 1:
                    # The first page has a simpler URL
                    page_url = base_url
                else:
                    page_url = f"{base_url}page/{page_num}/"
                
                print(f"\n--- Scraping Page {page_num}: {page_url} ---\n")

                try:
                    # Send a GET request to the page URL
                    response = requests.get(page_url, headers=headers)
                    response.raise_for_status()
                except requests.exceptions.HTTPError as e:
                    if e.response.status_code == 404:
                        print(f"Page {page_num} not found. Stopping.")
                        break # Exit the loop if the page doesn't exist
                    else:
                        raise # Re-raise other HTTP errors
                
                # Parse the HTML content of the page
                soup = BeautifulSoup(response.content, "html.parser")

                # Find all article entries on the page
                articles = soup.find_all("article")

                if not articles:
                    print(f"No articles found on page {page_num}. Stopping.")
                    break

                for article in articles:
                    # Extract the title and article URL
                    title_element = article.find("h3", class_="entry-title")
                    if title_element and title_element.find("a"):
                        title = title_element.get_text(strip=True)
                        article_url = title_element.find("a")["href"]

                        # Visit the article page to get the full content and image
                        try:
                            article_response = requests.get(article_url, headers=headers)
                            article_response.raise_for_status()
                            article_soup = BeautifulSoup(article_response.content, "html.parser")

                            # Extract the full content
                            content_element = article_soup.find("div", class_="entry-content")
                            content = ""
                            if content_element:
                                for script_or_style in content_element(["script", "style"]):
                                    script_or_style.decompose()
                                content = content_element.get_text(strip=True, separator="\n")

                            # Find the main image in the article
                            image_name = ""
                            if content_element:
                                image_element = content_element.find("img")
                                if image_element and image_element.get("src"):
                                    image_url = image_element["src"]
                                    image_url = urljoin(base_url, image_url)

                                    # Download the image
                                    try:
                                        image_response = requests.get(image_url, stream=True, headers=headers)
                                        image_response.raise_for_status()

                                        # Clean up the image filename
                                        image_basename = os.path.basename(image_url).split('?')[0]
                                        image_name = os.path.join("scraped_images", image_basename)

                                        with open(image_name, "wb") as f:
                                            for chunk in image_response.iter_content(1024):
                                                f.write(chunk)
                                        
                                        print(f"Image saved: {image_name}")

                                    except requests.exceptions.RequestException as e:
                                        print(f"Could not download image {image_url}. Error: {e}")
                            
                            # Write the collected data to the CSV file
                            csv_writer.writerow([title, content, image_name])
                            print(f"Title: {title}")
                            print(f"Content:\n{content[:200]}...")
                            print("-" * 20)

                        except requests.exceptions.RequestException as e:
                            print(f"Could not fetch article page {article_url}. Error: {e}")
                
                # Wait for a second before scraping the next page to be respectful to the server
                time.sleep(1)

    except requests.exceptions.RequestException as e:
        print(f"Could not connect to the website. Error: {e}")
    except IOError as e:
        print(f"Could not write to CSV file. Error: {e}")

if __name__ == "__main__":
    scrape_turnbackhoax()



--- Scraping Page 1: https://turnbackhoax.id/ ---

Image saved: scraped_images\HEADER-Dark-Background-16-1-678x381.png
Title: [SALAH] Video “Warga Malaysia Dukung Kemerdekaan Aceh”
Content:
Konten yang beredar merupakan hasil rekayasa AI, kemungkinan atau probabilitasnya mencapai 95,9 persen.
Unggahan video berisi klaim “warga Malaysia dukung kemerdekaan Aceh” adalah konten palsu (fabric...
--------------------
Image saved: scraped_images\HEADER-Dark-Background-31-678x381.png
Title: [SALAH] Video “Rudal R-Han Milik Indonesia”
Content:
Video yang beredar adalah hasil rekayasa AI.
Unggahan berisi klaim “rudal R-Han milik Indonesia” merupakan konten palsu (fabricated content).
Pada Senin (14/7/2025) akun Facebook “Mahfud Sidqi” membag...
--------------------
Image saved: scraped_images\HEADER-Dark-Background-30-678x381.png
Title: [SALAH] Menuang Tepung di Dekat Kompor Bisa Picu Ledakan Setara Bom
Content:
Faktanya, ledakan hanya mungkin terjadi bila tepung tersebar di udara dalam konsent

In [16]:
hoax_data

Empty DataFrame
Columns: [Title, Link, Image, Post_Date, Waktu_Scraping, Berita Hoax]
Index: []